In [1]:
import pandas as pd
import numpy as np
import pmdarima as pm
import plotly.graph_objects as go
import joblib

from statsmodels.tsa.statespace.sarimax import SARIMAX

# 1. Cargar y preparar el dataset

In [2]:
df = pd.read_csv('../Data/transformed/transformed_open_meteo.csv')
df['date'] = pd.to_datetime(df['date'])
df.set_index('date', inplace=True)
df.sort_index(inplace=True)
print("Dimensiones del dataset:", df.shape)

Dimensiones del dataset: (230796, 8)


# 2. Definir las variables a predecir (targets)

In [3]:
meteo_vars = ['temperature_2m_max', 'temperature_2m_min', 'temperature_2m_mean', 
              'windspeed_10m_max', 'precipitation_sum']

# 3. Obtener todas las provincias

In [4]:
provincias = df['provincia'].unique()

# 4. Detección de Outliers

- Método IQR

In [5]:
def detectar_outliers(series, threshold=1.5):
    q1 = series.quantile(0.25)
    q3 = series.quantile(0.75)
    iqr = q3 - q1
    limite_inferior = q1 - threshold * iqr
    limite_superior = q3 + threshold * iqr
    return (series < limite_inferior) | (series > limite_superior)

# 5. Auto Arima 

In [6]:
def ajustar_modelo_auto_arima(serie, exog_series, pasos_forecast=7, seasonal=True, m=7):
    model_auto = pm.auto_arima(
        serie, exogenous=exog_series, seasonal=seasonal, m=m,
        trace=False, error_action='ignore', suppress_warnings=True
    )
    order = model_auto.order
    seasonal_order = model_auto.seasonal_order
    print(f"    Parámetros: order={order}, seasonal_order={seasonal_order}")
    
    modelo = SARIMAX(serie, order=order, seasonal_order=seasonal_order)
    resultado = modelo.fit(disp=False)
    
    pred = resultado.get_forecast(steps=pasos_forecast)
    df_pred = pred.summary_frame()
    
    return df_pred, order, seasonal_order

In [7]:
test_period = 7

In [8]:
def save_model_provincia(predicciones_prov:dict, prov):
    if predicciones_prov:
        filename = f"predicciones_{prov}.pkl"
        joblib.dump(predicciones_prov, filename)
        print(f"Archivo '{filename}' guardado correctamente.")
    else:
        print(f"No se generaron predicciones para la provincia {prov}.")

# 6. Predicción

In [ ]:
for prov in provincias:
    print(f"\nProcesando provincia: {prov}")
    df_prov = df[df['provincia'] == prov].copy()
    
    # Preprocesar todas las variables meteorológicas: detección de outliers e imputación
    for var in meteo_vars:
        df_prov[var] = df_prov[var].mask(detectar_outliers(df_prov[var]))
        df_prov[var] = df_prov[var].interpolate(method='time')
        df_prov[var] = df_prov[var].fillna(method='bfill').fillna(method='ffill')
    
    # Diccionario para almacenar las predicciones de cada target en la provincia
    predicciones_prov = {}
    
    for target in meteo_vars:
        print(f"  Modelando target: {target}")
        exog_vars = [v for v in meteo_vars if v != target]

        fechas_unicas = np.sort(df_prov.index.unique())
        if len(fechas_unicas) <= test_period:
            print(f"    Insuficientes datos para train-test en {prov} - {target}")
            continue
        cutoff = fechas_unicas[-test_period]
        train_df = df_prov[df_prov.index < cutoff].copy()
        test_df  = df_prov[df_prov.index >= cutoff].copy()
        
        y_train = train_df[target]
        y_test  = test_df[target]
        exog_train = train_df[exog_vars]
        exog_test  = test_df[exog_vars]
        
        try:
            df_pred, order, seasonal_order = ajustar_modelo_auto_arima(y_train, exog_train,
                                                                       pasos_forecast=test_period,
                                                                       seasonal=True, m=7)
            df_pred.index = y_test.index
            
            df_pred_reset = df_pred.reset_index().rename(columns={'index': 'date'})
            
            df_pred_reset['provincia'] = prov
            df_pred_reset['target'] = target
            df_pred_reset['actual'] = y_test.values
            
            predicciones_prov[target] = df_pred_reset

            fig = go.Figure()
            train_reset = train_df.reset_index()
            test_reset = test_df.reset_index()
            
            fig.add_trace(go.Scatter(
                x=train_reset['date'], y=train_reset[target],
                mode='lines', name='Train'
            ))
            fig.add_trace(go.Scatter(
                x=test_reset['date'], y=test_reset[target],
                mode='lines', name='Test'
            ))
            fig.add_trace(go.Scatter(
                x=df_pred_reset['date'], y=df_pred_reset['mean'],
                mode='lines+markers', name='Forecast'
            ))
            fig.add_trace(go.Scatter(
                x=np.concatenate([df_pred_reset['date'], df_pred_reset['date'][::-1]]),
                y=np.concatenate([df_pred_reset['mean_ci_upper'], df_pred_reset['mean_ci_lower'][::-1]]),
                fill='toself',
                fillcolor='rgba(128,128,128,0.2)',
                line=dict(color='rgba(255,255,255,0)'),
                hoverinfo='skip',
                name='CI'
            ))
            fig.update_layout(
                title=f"Forecast de {target} en {prov}",
                xaxis_title="Date", yaxis_title=target
            )
            fig.show()
            
        except Exception as e:
            print(f"    Error en {prov} - {target}: {e}")

    save_model_provincia(predicciones_prov, prov)


Procesando provincia: A Coruña
  Modelando target: temperature_2m_max


C:\Users\a.escuredo\AppData\Local\Temp\ipykernel_4984\2275027449.py:9: FutureWarning: Series.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.
  df_prov[var] = df_prov[var].fillna(method='bfill').fillna(method='ffill')
C:\Users\a.escuredo\AppData\Local\Temp\ipykernel_4984\2275027449.py:9: FutureWarning: Series.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.
  df_prov[var] = df_prov[var].fillna(method='bfill').fillna(method='ffill')
C:\Users\a.escuredo\AppData\Local\Temp\ipykernel_4984\2275027449.py:9: FutureWarning: Series.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.
  df_prov[var] = df_prov[var].fillna(method='bfill').fillna(method='ffill')
C:\Users\a.escuredo\AppData\Local\Temp\ipykernel_4984\2275027449.py:9: FutureWarning: Series.fillna with 'method' is deprecated and will raise in a future versi

    Parámetros: order=(1, 1, 2), seasonal_order=(0, 0, 0, 7)


c:\Users\a.escuredo\AppData\Local\miniconda3\envs\weather_forecast\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: No frequency information was provided, so inferred frequency D will be used.
  self._init_dates(dates, freq)
c:\Users\a.escuredo\AppData\Local\miniconda3\envs\weather_forecast\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: No frequency information was provided, so inferred frequency D will be used.
  self._init_dates(dates, freq)


  Modelando target: temperature_2m_min


...

c:\Users\a.escuredo\AppData\Local\miniconda3\envs\weather_forecast\Lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning:

'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.

c:\Users\a.escuredo\AppData\Local\miniconda3\envs\weather_forecast\Lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning:

'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.

c:\Users\a.escuredo\AppData\Local\miniconda3\envs\weather_forecast\Lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning:

'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.

c:\Users\a.escuredo\AppData\Local\miniconda3\envs\weather_forecast\Lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning:

'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.

c:\Users\a.escuredo\AppData\Local\miniconda3\envs\weather_forecast\Lib\site-packages\sklearn\utils\d

    Parámetros: order=(2, 1, 2), seasonal_order=(1, 0, 2, 7)


c:\Users\a.escuredo\AppData\Local\miniconda3\envs\weather_forecast\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning:

No frequency information was provided, so inferred frequency D will be used.

c:\Users\a.escuredo\AppData\Local\miniconda3\envs\weather_forecast\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning:

No frequency information was provided, so inferred frequency D will be used.



Archivo 'predicciones_Melilla.pkl' guardado correctamente.

Procesando provincia: Murcia
  Modelando target: temperature_2m_max


C:\Users\a.escuredo\AppData\Local\Temp\ipykernel_4984\2275027449.py:9: FutureWarning:

Series.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.

C:\Users\a.escuredo\AppData\Local\Temp\ipykernel_4984\2275027449.py:9: FutureWarning:

Series.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.

C:\Users\a.escuredo\AppData\Local\Temp\ipykernel_4984\2275027449.py:9: FutureWarning:

Series.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.

C:\Users\a.escuredo\AppData\Local\Temp\ipykernel_4984\2275027449.py:9: FutureWarning:

Series.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.

C:\Users\a.escuredo\AppData\Local\Temp\ipykernel_4984\2275027449.py:9: FutureWarning:

Series.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffi